In [1]:
import sys
sys.path.append('/Users/vandanchopra/Vandan_Personal_Folder/CODE_STUFF/Projects/mathematricks/')
import os
import pickle
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
from pathlib import Path
import yfinance as yf
import time
from datetime import timedelta, datetime
from systems.performance_reporter import PerformanceReporter

from systems.utils import MarketDataExtractor

In [2]:
market_data_extractor = MarketDataExtractor()
strategy_reporter = PerformanceReporter(market_data_extractor)

# Inputs

In [25]:
testname = 'c1ff5702001d336df59c25617f6918a3badf49c4944d32ed2d736f7c3d24f1fa_5' # Profits Reinvested & Margin Deployed @ 0.65 of 3.3x (exit on daily close, fill price is daily close)
save_folder = "/Users/vandanchopra/Vandan_Personal_Folder/CODE_STUFF/Projects/mathematricks/db/data/ibkr/1d"
test_folder_path = f'/Users/vandanchopra/Vandan_Personal_Folder/CODE_STUFF/Projects/mathematricks/db/vault/backtest_reports/{testname}'
indices = ["^DJI", "^IXIC", "^GSPC"]
starting_capital = 72463 * 3

In [26]:
# testname = '4c4f66a4e5697c5342a7e4dee1e145be8a85d133a7300ee6505a13895989a8e7' # Profits not Reinvested
backtest_output = strategy_reporter.load_backtest_output(test_folder_path)
open_orders = backtest_output['open_orders']
closed_orders = backtest_output['closed_orders']
config_dict = backtest_output['config_dict']
figures = []

In [27]:
#Processing Open order to make them close, and remove history
open_orders_list = strategy_reporter.clean_up_order_list(open_orders, drop_history=True)
#Processing Closed orders to remove history
closed_orders_list = strategy_reporter.clean_up_order_list(closed_orders, drop_history=True)
#Merge both orders
final_list = closed_orders_list + open_orders_list
# Step 2: Sort the filtered orders by exit order `filled_timestamp`
sorted_orders = sorted(final_list, key=lambda x: x[1]['filled_timestamp'])
# Step 3: Fetch the first and last `filled_timestamp` with buffer
start_date = sorted_orders[0][1]['filled_timestamp'] - timedelta(days=365)
end_date = sorted_orders[-1][1]['filled_timestamp'] + timedelta(days=365)
# end_date = pd.Timestamp(datetime(2010, 1, 1))
# Current we are downloading csv file for below three index
index_data_dict = strategy_reporter.load_and_save_index_data(indices, start_date, end_date, save_folder)
rolling_window = int(max(60, (end_date - start_date).days / 20))
print(f"Analyzing Data with a rolling window of: {rolling_window} days")

Analyzing Data with a rolling window of: 310 days


### Equity Curve

In [28]:
# Drawdown analysis and Equity Curve should be on a day to day basis with open_position values updated on a daily basis based on the symbol_ltp mentioned on each order
trade_df_by_date = strategy_reporter.create_data_input_for_cumulative_returns_and_indices(final_list, index_data_dict, starting_capital)
# strategy_reporter.plot_cumulative_returns_and_indices(trade_df_by_date, index_data_dict)
figures.append(strategy_reporter.plot_cumulative_returns_and_indices(trade_df_by_date, index_data_dict))

In [29]:
# Log Curve of Cumulative Returns
trade_df_by_date['log_growth'] = np.log(trade_df_by_date['cumulative_return'])
log_index_data = np.log(index_data_dict['^IXIC']['adj close'])
figures.append(strategy_reporter.plot_cumulative_returns_log_scale(trade_df_by_date['log_growth'], log_index_data))

/Users/vandanchopra/Vandan_Personal_Folder/CODE_STUFF/Projects/mathematricks/systems/performance_reporter.py:516: FutureWarning:

Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`

/Users/vandanchopra/Vandan_Personal_Folder/CODE_STUFF/Projects/mathematricks/systems/performance_reporter.py:517: FutureWarning:

Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`



# Plot Rolling charts

#### Sharpe Ratio

In [30]:
account_value = trade_df_by_date['account_value']
index_name = '^IXIC'
index_value = index_data_dict[index_name]['close']
risk_free_rate=0.0415
# rename 'close' to '^IXIC' in index_value
index_value = index_value.rename(index_name)
rolling_sharpe, rolling_sharpe_index, absolute_sharpe_ratio, absolute_sharpe_ratio_index = strategy_reporter.calculate_rolling_sharpe_ratio(account_value, index_value, risk_free_rate=risk_free_rate, window=rolling_window)
figures.append(strategy_reporter.plot_rolling_sharpe_ratio(rolling_sharpe, rolling_sharpe_index, absolute_sharpe_ratio, absolute_sharpe_ratio_index, risk_free_rate, window=rolling_window))

### Rolling Win Percentage

In [9]:
trade_df_by_order = strategy_reporter.prepare_trade_data_df_by_order(final_list)
# figures.append(strategy_reporter.plot_rolling_win_percentage(trade_df_by_order, index_data_dict, window=rolling_window))
figures.append(strategy_reporter.plot_rolling_win_percentage(trade_df_by_order, index_data_dict, window=90))

### Rolling Risk Reward Ratio

In [10]:
rolling_risk_reward_ratio, rolling_risk_reward_ratio_long, rolling_risk_reward_ratio_short = strategy_reporter.calculate_rolling_risk_reward_ratio(trade_df_by_order, window=rolling_window)
figures.append(strategy_reporter.plot_rolling_risk_reward_ratio(rolling_risk_reward_ratio, rolling_risk_reward_ratio_long, rolling_risk_reward_ratio_short, rolling_window, index_data_dict))

### Drawdown Analysis

In [11]:
trade_df_by_date_drawdown = strategy_reporter.calculate_drawdowns(trade_df_by_date)
figures.append(strategy_reporter.plot_drawdown(trade_df_by_date_drawdown, index_data_dict))

### Plot Trades of a Single Asset

In [12]:
from pprint import pprint
# Add order_num to the final_list
for order_num, order in enumerate(final_list):
    for i in range(len(order)):
        order[i]['order_num'] = order_num

# Get list of all the symbols in final_list
all_symbols = list(set([x[1]['symbol'] for x in final_list]))
# from pprint import pprint
pprint(str(all_symbols))

("['APP', 'LYG', 'SPGI', 'DD', 'IQV', 'TTWO', 'KHC', 'KLAC', 'F', 'NGG', "
 "'APD', 'ETR', 'TCOM', 'INFY', 'SHEL', 'ETN', 'NKE', 'IBN', 'MTB', 'CTSH', "
 "'DUK', 'ARGX', 'TAK', 'MO', 'BK', 'BP', 'TMUS', 'UNP', 'STZ', 'SCCO', "
 "'CMCSA', 'CM', 'AJG', 'NSC', 'CNQ', 'UPS', 'ISRG', 'APO', 'SE', 'RY', 'MAR', "
 "'HWM', 'CTVA', 'DOW', 'ASML', 'PEG', 'AMT', 'SNOW', 'ABBV', 'PRU', 'AMP', "
 "'YUM', 'HD', 'BX', 'MS', 'V', 'EQNR', 'JCI', 'CMI', 'AIG', 'EW', 'CP', "
 "'GRMN', 'HCA', 'KMB', 'ABNB', 'ENB', 'TSM', 'CI', 'MMM', 'AEM', 'TRI', "
 "'SHW', 'CVX', 'JD', 'DELL', 'GOOGL', 'SPG', 'BMO', 'RIO', 'ALL', 'MSI', "
 "'MET', 'MCK', 'AEP', 'HSBC', 'IDXX', 'TSLA', 'LNG', 'SHOP', 'PG', 'NWG', "
 "'AMZN', 'FITB', 'STLA', 'T', 'DIS', 'CAT', 'CUK', 'MA', 'NDAQ', 'DASH', "
 "'MPC', 'SAN', 'ZTS', 'AMGN', 'GEHC', 'IT', 'CCL', 'INTC', 'SNPS', 'PFE', "
 "'COR', 'PLD', 'COST', 'TRP', 'DLR', 'NOC', 'CVNA', 'FCNCA', 'GILD', 'NVO', "
 "'ED', 'XYL', 'NOW', 'BNS', 'PCG', 'LULU', 'WMT', 'ARES', 'VRT', 'ONON', "
 "'

In [13]:
# Add order_num to the final_list
for order_num, order in enumerate(open_orders_list):
    for i in range(len(order)):
        order[i]['order_num'] = order_num

# Get list of all the symbols in final_list
open_symbols = list(set([x[1]['symbol'] for x in open_orders_list]))
from pprint import pprint
pprint(str(open_symbols))

("['VRT', 'JCI', 'MSTR', 'SE', 'AMGN', 'DELL', 'ALL', 'ANET', 'FICO', 'UBS', "
 "'PDD', 'HSY', 'CRWD', 'ZS', 'VST']")


In [20]:
import random
symbol = random.choice(all_symbols)
print({'symbol':symbol})
if symbol in all_symbols:
    strategy_reporter.process_and_plot_orders(final_list, symbol, save_folder)
else:
    print(f"Symbol {symbol} not found in the final list of orders")

{'symbol': 'AMD'}


In [15]:
count = 16
((final_list[count][-1]['fill_price'] - final_list[count][0]['fill_price'])/final_list[count][0]['fill_price'])*100

2.4866785079929055

In [16]:
closed_orders[count][0]['symbol_ltp']

{'2009-01-12 23:59:59+00:00': 28.15}

In [17]:
closed_orders[15]

[{'symbol': 'DAL',
  'timestamp': Timestamp('2009-01-02 23:59:59+0000', tz='UTC'),
  'orderDirection': 'BUY',
  'entryPrice': 10.27,
  'orderType': 'MARKET',
  'timeInForce': 'GTC',
  'orderQuantity': 973.0,
  'strategy_name': 'strategy_5_1_4',
  'broker': 'SIM',
  'granularity': '1d',
  'status': 'closed',
  'signal_id': '34138402abeec78db278244cf91a7a5719a1110a4a29a6a9dcf96c869f54f753',
  'symbol_ltp': {'2009-01-02 23:59:59+00:00': 10.27},
  'decision_matrix':      symbol_ltp  short_sma_trimmed  long_sma_trimmed  trend_strength  \
  DAL       10.27           8.742111          8.176444        1.069182   
  MELI      14.23          14.614222         23.041889        0.634246   
  CI         15.4          19.438889         28.851167        0.673764   
  CBRE       3.96           6.309556         11.034333        0.571811   
  BX         5.64           8.342667         12.613833        0.661390   
  VALE      11.28          12.656111         19.952556        0.634310   
  CMI       24.84

# Save all Figures to HTML

In [18]:
strategy_reporter.save_to_html_file(figures, testname, test_folder_path, strategies=config_dict['strategies'])

HTML file saved: 
/Users/vandanchopra/Vandan_Personal_Folder/CODE_STUFF/Projects/mathematricks/db/vault/backtest_reports/c1ff5702001d336df59c25617f6918a3badf49c4944d32ed2d736f7c3d24f1fa/backtest_figures.html
